# Preparation

First of all we need to create a folder for the project and copy files from this repository there.
To try this notebook, at least [Miniconda](https://docs.conda.io/en/main/miniconda.html) should be installed.
Microsoft Visual C++ 14.0 or greater may be required.
Get it with ["Microsoft C++ Build Tools"]( https://visualstudio.microsoft.com/visual-cpp-build-tools/).
During the installation don't forget to click `modify` and tick "Desktop development with C++".

I recommend to create a virtual environment.
To generate it right in the project folder, open Anaconda prompt and type:
* `cd path_to_your_folder`
* `conda env create --prefix ./env --file environment.yaml`, then follow instructions in a window. The environment will be created in the env folder, the modules from `environment.yaml` will be installed.
* activate the environment typing `conda activate ./env`.
* run `jupyter notebook` and open this notebook. 

A note regarding `onnxruntime` - there is an option to use GPU instead CPU to get higher performance, but it will not be considered here.

If everything is successful, let's get the main model.
We will use and [inswapper_128.onnx](https://huggingface.co/deepinsight/inswapper/resolve/main/inswapper_128.onnx) to perform face swap.
Download it and drop in the project folder.

Folder system:
* `gifs` - contains GIFs to swap face in
* `faces` - contains photos of our victims
* `output` - stores results
* `env` - Python environment
* `temp` - to keep frames from GIFs

# Modules

In [1]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import onnxruntime
import insightface
import glob
from IPython.display import display, clear_output, HTML
import json
import ipywidgets as widgets
import numpy as np
from numpy.linalg import norm
import functools
import os
import shutil
import base64

from PIL import Image, ImageFile
ImageFile.LOAD_TRUNCATED_IMAGES = True

# Functions

## Read and write images

`insightface` requires input images to be in `numpy.array` format.
We could install `opencv-python`, but we don't look for easy ways here.
 
We need two functions.
One will use `PIL` to read the image and convert it to RGB, then we apply `np.array`.
Another function will convert the image back to `PIL` format and save result.  

In [2]:
def read_img(path_to_img):
    with Image.open(path_to_img) as img:
        return np.array(img.convert('RGB'))
    
def save_img(arr_img, path_to_save):
    img = Image.fromarray(arr_img) # convert back to PIL format
    img.save(path_to_save)

## GIF handling

Sometimes GIF are in WEBP format.
Simple renaming will not help, here is how to convert them.

In [3]:
def webp_to_gif(path='./gifs/*.webp'):
    for i in glob.glob('./gifs/*.webp'):
        try:
            with Image.open(path) as im:
                im.info.pop('background', None)
                im.save(path[:-4] + 'gif', 'gif', save_all=True)
            os.remove(i)
        except Exception:
            print(f'[Error] {i} was not converted')

Face swap will be performed frame by frame.
We need to extract frames from our GIF-file and save its duration to reconstruct GIF later.

In [4]:
def extract_frames(path_to_gif):
    with Image.open(path_to_gif) as gif:
        gif_duration = gif.info['duration']
    
        # save frames one by one
        for frame in range(0, gif.n_frames):
            gif.seek(frame)
            gif.save('temp/{}.png'.format(str(frame).zfill(4))) # to keep name like 0001.png
            
    return gif_duration

After we have performed face swap we need to recreate the GIF.

In [5]:
def create_gif(path_to_save, gif_duration):
    frames = [Image.open(name) for name in glob.glob('./temp/*')]
    frames[0].save(
        path_to_save,
        save_all=True,
        format='GIF',
        append_images=frames[1:],
        optimize=False,
        duration=gif_duration,
        loop=0
        )

## Dealing with faces

Here I see two main tasks:
* We need to find a face in a source picture and a target picture
* We need to swap faces

Let's assume I have a lot of friends and I need some help with a choice.
We will:
1. Get a list of all faces in `./faces` folder
2. Compare them with a target
3. Sort faces based on similarity

First step is time consuming, so we get face embeddings once and save them to JSON file to use later.

So, let's start.
The function `get_face` will apply chosen `face_analyser` to get a list of faces in a picture (if there are any). 

In [6]:
def get_face(img_data, face_analyser):
    analysed = face_analyser.get(img_data)
    try:
        return sorted(analysed, key=lambda x: x.bbox[0])
    except IndexError:
        return None

Having `get_face` we can get the database of face embeddings.

In [7]:
def create_face_db(face_analyser):
    faces = {}
    for i in glob.glob('./faces/*.jpg'):
        img = read_img(i)
        try:
            faces[i] = [float(_) for _ in get_face(img, face_analyser)[0]['embedding']]
        except IndexError:
            print(f'No face found in {i}')

    with open('./faces/embeddings.json', 'w') as outfile:
        json.dump(faces, outfile)

Face embeddings, which are vectors, will be used to compare faces.
The task of comparison is reduced to computing the Euclidean distance $d$ between two vectors:

$$d(\vec{x}, \vec{y}) = \sqrt{(x_1 - y_1)^2 + (x_2 - y_2)^2 ... (x_n - y_n)^2}$$

where $x_1$, $x_2$...$x_n$ and $y_1$, $y_2$...$y_n$ are "coordinates" of target vectors $\vec{x}$ and $\vec{y}$ respectively.

We will not implement the formula and use `numpy.linalg.norm` having same functionality.

The function `get_similar_face()` will:
* use `get_face()` to find all faces in the target picture/GIF
* get target face embeddings
* compute distances between target face embeddings and those from the face database
* sort the database of faces based on distances, ascending
* if no face found in the first frame of the GIF, then return a sorted list of faces from the database

In [8]:
def get_similar_faces(faces, target):
    face_embeddings = []
    # get embeddings for each face in target
    faces_in_target = get_face(read_img(target), face_analyser)
    if faces_in_target:
        for face in faces_in_target:
            source = face['embedding']

            # compute distances
            path, distance = [], []
            for key, val in faces.items():
                path.append(key)
                distance.append(norm(np.array(val) - np.array(source)))

            # sort by distance
            face_embeddings.append([x for _, x in sorted(zip(distance, path))])
    else:
        # if no face found in 1st GIF frame, then just return sorted list of faces available
        face_embeddings.append(sorted(faces.keys()))

    return face_embeddings

And finally, the key function `swap_faces()`:
* get a face from the source picture
* clean the `temp` folder
* extract frames from the target GIF to the `temp` folder
* swap faces frame by frame using the model in `face_swapper` and replacing old frames by new ones
* reconstruct a GIF from new frames

We will also print a counter to the output to see a progress.

In [9]:
def swap_faces(source, target, face_analyser, face_swapper, face_index, output=None):
    '''
    source, str: path to a source image to take a face from
    target, str: path to a target GIF
    face_analyser: a model to analyse faces in a picture
    face_swapper: a model to perform face swap
    face_index, int: an index of a face to swap
    --
    swap faces in source and target
    '''
    source_face = get_face(read_img(source), face_analyser)[0]
    # clean temp folder
    [os.remove(file) for file in glob.glob('./temp/*')]
    
    gif_duration = extract_frames(target)
    
    reface_images = glob.glob('temp/*')
    for ind, img in enumerate(reface_images):
        if output:
            with output:
                print(f'{ind + 1} out of {len(reface_images)}')
                output.clear_output(wait=True)
        frame = read_img(img)
        try:
            face = get_face(frame, face_analyser)[face_index]
            result = face_swapper.get(frame, face, source_face, paste_back=True)
            save_img(result, img)
        except IndexError: # if no face found in target, then skip
            pass
            
    output_path = './output/' + source.split('\\')[-1] + target.split('\\')[-1]
    create_gif(output_path, gif_duration)
    
    if output:
        with output:
            clear_output(wait=True)
            print('Done')
    return output_path

# Model loading and gif preprocessing

In [10]:
# get the list of registered execution providers
providers = onnxruntime.get_available_providers()

# prepare our models
face_swapper = insightface.model_zoo.get_model('inswapper_128.onnx', providers=providers)
face_analyser = insightface.app.FaceAnalysis(name='buffalo_l', providers=providers)
face_analyser.prepare(ctx_id=0, det_size=(640, 640))

webp_to_gif() # convert gifs to correct format
clear_output()

In [11]:
create_face_db(face_analyser) # commented because should be used once
# load face embeddings
with open('./faces/embeddings.json', 'r') as file:
    faces = json.load(file)

# Interface

Now let's create simple interface.
I will use `ipywidgets` library.
Two dropdowns for GIFs and for sorted faces, one button to start face swap and another one will be exclusively for swaping my own face.
It would also be nice to show previews.
GIF may contains several faces.
The one of interest will be chosen using slider. 

In [12]:
menu = widgets.Dropdown(
       options=glob.glob('./gifs/*.gif') + glob.glob('./output/*.gif'),
       description='GIFs:'
)
face_menu = widgets.Dropdown(
       options=glob.glob('./faces/*.jpg'),
       description='Faces:'
) 
face_slider = widgets.IntSlider(value=0, min=0, max=0, description="Which face?")

me_but = widgets.Button(description='Place myself!')
swap_but = widgets.Button(description="Let's go!")

# create dummy image temp.jpg
Image.new('RGB', (300, 300), (255, 255, 255)).save('temp.jpg', 'JPEG')
with open('temp.jpg', 'rb') as im:
    thumb = im.read()

gif_frame = widgets.Image(
    value=thumb,
    format='png',
    width=300,
    height='auto'
)

face_frame = widgets.Image(
    value=open(face_menu.value, 'rb').read(),
    format='png',
    width=300,
    height='auto'
)

# gather everything in one box
output = widgets.Output() # here we will display things
box = widgets.VBox([
    widgets.HBox([menu, face_menu]),
    widgets.HBox([gif_frame, face_frame]),
    face_slider,
    widgets.HBox([swap_but, me_but]),
    output
])

We need functions providing interaction with widgets.
There will be three of them:
1. Sorting the list of closest faces and updating a GIF preview based on a chosen item in the `menu` GIF dropdown and a face in the slider `face_slider`
2. Updating face preview based on the value in `face_menu` dropdown
3. Performing face swap when we press `me_but` or `swap_but`

In [13]:
def update_face_list(change, slider_change=False):
    with Image.open(menu.value) as temp_im:
        temp_im.convert('RGB').save('./temp.jpg')
        
    with open('./temp.jpg', 'rb') as temp_im:
        gif_frame.value = temp_im.read()
    
    if not slider_change:
        face_slider.max = len(get_face(read_img('temp.jpg'), face_analyser)) - 1
        face_slider.value = 0
        
    face_menu.options = get_similar_faces(faces, 'temp.jpg')[face_slider.value]
        
        
def update_face_preview(change):
    face_frame.value = open(face_menu.value, 'rb').read()
    

def run_swap(button, me=None):
    chosen_face = face_menu.value
    if me:
        chosen_face = './faces\\me.jpg'
    chosen_gif = menu.value
    
    # swap faces and get path to the new GIF
    result_path = swap_faces(chosen_face, chosen_gif, face_analyser, face_swapper, face_slider.value, output)
    
    # show swap result
    with output:
        b64 = base64.b64encode(open(result_path,'rb').read()).decode('ascii')
        display(HTML(f'<img src="data:image/gif;base64,{b64}" />'))
        
    # include swapped GIF in menu in case we want to swap another face on it
    menu.options = glob.glob('./gifs/*.gif') + glob.glob('./output/*.gif')
    menu.value = chosen_gif # set the current gif back as an active item

# Swap faces

Now let's finally display the interface and try to swap some faces.
I hired some artificial co-workers using [this-person-does-not-exist](https://this-person-does-not-exist.com/en) service.
Their names were generated in [behindthename](https://www.behindthename.com/). GIFs were downloaded from [giphy](https://giphy.com/).

In [14]:
# track dropdown and slider changes
menu.observe(update_face_list, names='value')
face_menu.observe(update_face_preview, names='value')
face_slider.observe(functools.partial(update_face_list, slider_change=True), names='value')

# button interactions
swap_but.on_click(functools.partial(run_swap, me=None))
me_but.on_click(functools.partial(run_swap, me=True))

# prepare interface for the first gif
update_face_list(0) 
box

If widgets are not shown (and you use virtual environment), uncomment and run command `!jupyter nbextension enable --py --sys-prefix widgetsnbextension` in the cell and relaunch the notebook. 